In [31]:
import os
import zipfile
%load_ext autoreload

%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [32]:
import tracemalloc
import psutil
import pprint
import pandas as pd
import uuid
import json
import os
import glob
import re
import sys
from bs4 import NavigableString, BeautifulSoup
from collections import defaultdict
import random
import string
import time

from utils.config import config
from utils.logger.logger import loggerCreator

# ePI Modules
from parse.rulebook.rulebook import StyleRulesDictionary

from parse.extractor.parser import parserExtractor
from match.matchDocument.matchDocument import MatchDocument
from documentAnnotation.documentAnnotation import DocumentAnnotation
from htmlDocTypePartitioner.partition import DocTypePartitioner
from extractContentBetweenHeadings.dataBetweenHeadingsExtractor import DataBetweenHeadingsExtractor
from fhirXmlGenerator.fhirXmlGenerator import FhirXmlGenerator
from fhirService.fhirService import FhirService
from utils.logger.matchLogger import MatchLogger
from languageInfo.documentTypeNames.documentTypeNames import DocumentTypeNames
from listBundle.addAndUpdateListBundle.addAndUpdateListBundle import ListBundleHandler

class FolderNotFoundError(Exception):
    pass

class Metrics:
    
    def __init__(self, logFileName, logger):
        self.logFileName = logFileName
        self.start()
        self.writer = open(self.logFileName, 'a')
        self.writer.write("StepName,Time,Current Memory,Peak Memory,Used Ram Percentage\n")
        self.finalPeak = 0
        self.finalTotalTime = 0
        self.finalUsedRamPerc = 0
        self.logger = logger
    
    def start(self):
        self.startTime = time.time()
        tracemalloc.start()
    
    def getMetric(self, msg):
        
        self.endTime = time.time()
        
        self.totalTime = self.endTime - self.startTime
        
        
        current, peak = tracemalloc.get_traced_memory()
        current = current / 10**6
        peak = peak / 10**6
        
        usedRamPerc = psutil.virtual_memory()[2]
        
        self.finalPeak = max(self.finalPeak, peak)
        self.finalUsedRamPerc = max(self.finalUsedRamPerc, usedRamPerc)

        self.finalTotalTime = self.finalTotalTime + self.totalTime
        #self.finalTotalTime = round(self.finalTotalTime/60,3)
        
        outputString = f"{msg},{round(self.totalTime/60,4)} Min,{current} MB,{peak} MB,{usedRamPerc}%\n"
        
        self.logger.logFlowCheckpoint(f"{outputString}")
        
        print(f"Metrics : {outputString}")
        self.writer.write(outputString)
        tracemalloc.stop()
        tracemalloc.start()
        self.startTime = time.time()
    def end(self):
        
        current, peak = tracemalloc.get_traced_memory()
        current = current / 10**6
        outputString = f"Final Metrics,{round(self.finalTotalTime/60,4)} Min,{current} MB,{self.finalPeak} MB,{self.finalUsedRamPerc}%\n"
        print(f"Metrics : {outputString}")
        self.logger.logFlowCheckpoint(f"{outputString}")
        self.writer.write(outputString)
        self.writer.close()
        tracemalloc.stop()
        
        


def convertToInt(x):
    try:
        return str(int(x))
    except:
        return x


def convertCollectionToDataFrame(collection):

    dfExtractedHier = pd.DataFrame(collection)
    dfExtractedHier['parent_id'] = dfExtractedHier['parent_id'].apply(
        lambda x: convertToInt(x))
    dfExtractedHier['id'] = dfExtractedHier['id'].apply(
        lambda x: convertToInt(x))

    return dfExtractedHier

def getRandomString(N):
    str_ = ''.join(random.choice(string.ascii_uppercase + string.digits
                                 + string.ascii_lowercase) for _ in range(N))
    return str_


def convertHtmlToJson(controlBasePath, basePath, domain, procedureType, languageCode, htmlDocName, fileNameQrd, fileNameLog):

    module_path = os.path.join(basePath)

    if "/" in basePath:
        pathSep = "/"
    else:
        pathSep = "\\"
    
    # Generate output folder path
    output_json_path = os.path.join(basePath, 'outputJSON')

    """
        Check if input folder exists, else throw exception
    """
    if(os.path.exists(module_path)):
        filenames = glob.glob(os.path.join(module_path, htmlDocName))

        # Create language specific folder in outputJSON folder if it doesn't exist
        if(not os.path.exists(output_json_path)):
            os.mkdir(output_json_path)
        logger = MatchLogger(f'Parser_{getRandomString(1)}', htmlDocName,
                             domain, procedureType, languageCode, "HTML", fileNameLog)

        styleLogger = MatchLogger(
            f'Style Dictionary_{getRandomString(1)}', htmlDocName, domain, procedureType, languageCode, "HTML", fileNameLog)

        styleRulesObj = StyleRulesDictionary(logger=styleLogger,
                                             controlBasePath=controlBasePath,
                                             language=languageCode,
                                             fileName=fileNameQrd,
                                             domain=domain,
                                             procedureType=procedureType
                                             )

        parserObj = parserExtractor(config, logger, styleRulesObj.styleRuleDict,
                                    styleRulesObj.styleFeatureKeyList,
                                    styleRulesObj.qrd_section_headings)

        for input_filename in filenames:
          # if(input_filename.find('Kalydeco II-86-PI-clean')!=-1):
            output_filename = os.path.join(output_json_path, htmlDocName)
            style_filepath =  output_filename.replace('.html','.txt')
            style_filepath =  style_filepath.replace('.txtl','.txt')
            style_filepath =  style_filepath.replace('.htm','.txt')
            print("-------------",style_filepath,"-----------------")

            output_filename = output_filename.replace('.html', '.json')
            output_filename = output_filename.replace('.htm', '.json')
            print(input_filename, output_filename)
            parserObj.createPIJsonFromHTML(input_filepath=input_filename,
                                           output_filepath=output_filename,
                                           style_filepath = style_filepath,
                                           img_base64_dict=parserObj.convertImgToBase64(input_filename)
                                           )
            
        return output_filename.split(pathSep)[-1], style_filepath
    else:
        try:    
            raise FolderNotFoundError(module_path + " not found")
        except:  
            logger.logFlowCheckpoint("Folder For Language Code Not Found In Input File")
            logger.logException("Folder For Language Code Not Found In Input File")
        raise FolderNotFoundError(module_path + " not found")
        return None


def splitJson(controlBasePath, basePath, domain, procedureType, languageCode, fileNameJson, fileNameQrd, fileNameLog):

    styleLogger = MatchLogger(
        f'Style Dictionary_{getRandomString(1)}', fileNameJson, domain, procedureType, languageCode, "Json", fileNameLog)

    styleRulesObj = StyleRulesDictionary(logger=styleLogger,
                                        controlBasePath=controlBasePath,
                                        language=languageCode,
                                        fileName=fileNameQrd,
                                        domain=domain,
                                        procedureType=procedureType
                                        )
    
    path_json = os.path.join(basePath,'outputJSON', fileNameJson)
    print("PathJson",path_json)
    partitionLogger = MatchLogger(
        f'Partition_{getRandomString(1)}', fileNameJson, domain, procedureType, languageCode, "Json", fileNameLog)

    partitioner = DocTypePartitioner(partitionLogger)

    partitionedJsonPaths = partitioner.partitionHtmls(
        styleRulesObj.qrd_section_headings, path_json)

    return partitionedJsonPaths


def extractAndValidateHeadings(controlBasePath,
                                basePath,
                                domain,
                                procedureType,
                                languageCode,
                                documentNumber,
                                fileNameDoc,
                                fileNameQrd,
                                fileNameMatchRuleBook,
                                fileNameDocumentTypeNames,
                                fileNameLog,
                                stopWordFilterLen=6,
                                isPackageLeaflet=False,
                                medName=None
                                ):

    if documentNumber == 0:
        topHeadingsConsidered = 4
        bottomHeadingsConsidered = 6
    elif documentNumber == 1:
        topHeadingsConsidered = 3
        bottomHeadingsConsidered = 5
    elif documentNumber == 2:
        topHeadingsConsidered = 5
        bottomHeadingsConsidered = 15
    else:
        topHeadingsConsidered = 5
        bottomHeadingsConsidered = 10

    print(f"Starting Heading Extraction For File :- {fileNameDoc}")
    logger = MatchLogger(f"Heading Extraction {fileNameDoc}_{getRandomString(1)}", fileNameDoc, domain, procedureType, languageCode, documentNumber, fileNameLog)
    logger.logFlowCheckpoint("Starting Heading Extraction")

    stopWordlanguage = DocumentTypeNames(
        controlBasePath=controlBasePath,
        fileNameDocumentTypeNames=fileNameDocumentTypeNames,
        languageCode=languageCode,
        domain=domain,
        procedureType=procedureType,
        documentNumber=documentNumber
        ).extractStopWordLanguage()

    matchDocObj = MatchDocument(
        logger,
        controlBasePath,
        basePath,
        domain,
        procedureType,
        languageCode,
        documentNumber,
        fileNameDoc,
        fileNameQrd,
        fileNameMatchRuleBook,
        fileNameDocumentTypeNames,
        topHeadingsConsidered,
        bottomHeadingsConsidered,
        stopWordFilterLen,
        stopWordlanguage,
        isPackageLeaflet,
        medName)
    df, coll, documentType = matchDocObj.matchHtmlHeaddingsWithQrd()

    return df, coll, documentType


def parseDocument(controlBasePath,
                  basePath,
                  htmlDocName,
                  fileNameQrd,
                  fileNameMatchRuleBook,
                  fileNameDocumentTypeNames,
                  jsonTempFileName,
                  listBundleDocumentTypeCodesFileName,
                  apiMmgtBaseUrl,
                  getListApiEndPointUrlSuffix,
                  addUpdateListApiEndPointUrlSuffix,
                  addBundleApiEndPointUrlSuffix,
                  apiMmgtSubsKey,
                  medName = None):
    
    listRegulatedAuthCodesAccrossePI = []
    
    if "/" in basePath:
        pathSep = "/"        
    else:
        pathSep = "\\"
    
    fileNameLog = os.path.join(basePath,'FinalLog.txt')

    pathComponents = basePath.split(pathSep)
    print(pathComponents, htmlDocName)
    timestamp = pathComponents[-1]
    languageCode =  pathComponents[-2]
    medName = pathComponents[-3]
    procedureType = pathComponents[-4]
    domain = pathComponents[-5]

    print(timestamp, languageCode, medName, procedureType, domain)
        
    flowLogger =  MatchLogger(f"Flow Logger HTML_{getRandomString(1)}", htmlDocName, domain, procedureType, languageCode, "HTML", fileNameLog)
    
    metrics = Metrics(os.path.join(basePath,'Metrics.csv'),flowLogger)
    
    
    flowLogger.logFlowCheckpoint("Starting HTML Conversion To Json")
    ###Convert Html to Json
    fileNameJson, stylesFilePath = convertHtmlToJson(controlBasePath, basePath, domain, procedureType, languageCode, htmlDocName, fileNameQrd, fileNameLog)
    
    print("stylePath:-",stylesFilePath)
    flowLogger.logFlowCheckpoint("Completed HTML Conversion To Json")
    metrics.getMetric("HTML Conversion To Json")

    flowLogger.logFlowCheckpoint("Starting Json Split")

    ###Split Uber Json to multiple Jsons for each category.
    partitionedJsonPaths = splitJson(controlBasePath, basePath, domain, procedureType, languageCode, fileNameJson, fileNameQrd, fileNameLog)
    
    partitionedJsonPaths = [ path.split(pathSep)[-1] for path in partitionedJsonPaths]
    flowLogger.logFlowCheckpoint(str(partitionedJsonPaths))
    
    flowLogger.logFlowCheckpoint("Completed Json Split")
    metrics.getMetric("Split Json")
    
    flowLogger.logFlowCheckpoint("Started Processing Partitioned Jsons")
    
    for index, fileNamePartitioned in enumerate(partitionedJsonPaths):
        #print("Index", index)
        #if index in [2,3]:
        #    continue
        
        flowLogger.logFlowCheckpoint(f"\n\n\n\n||||||||||||||||||||||||||||||||{str(index)} ||||| {str(fileNamePartitioned)}||||||||||||||||||||||||||||||||\n\n\n\n")
        
        if index == 3:
            stopWordFilterLen = 100
            isPackageLeaflet = True
        else:
            stopWordFilterLen = 6
            isPackageLeaflet = False
            
        df, coll, documentType = extractAndValidateHeadings(controlBasePath,
                                    basePath,
                                    domain,
                                    procedureType,
                                    languageCode,
                                    index,
                                    fileNamePartitioned,
                                    fileNameQrd,
                                    fileNameMatchRuleBook,
                                    fileNameDocumentTypeNames,
                                    fileNameLog,
                                    stopWordFilterLen=stopWordFilterLen,
                                    isPackageLeaflet=isPackageLeaflet,
                                    medName=medName)
    
        
        print(f"Completed Heading Extraction For File")
        flowLogger.logFlowCheckpoint("Completed Heading Extraction For File")
        metrics.getMetric(f"{index}: Heading Extraction")

        print(f"Starting Document Annotation For File :- {fileNamePartitioned}")        
        flowLogger.logFlowCheckpoint("Starting Document Annotation For File")
        documentAnnotationObj = DocumentAnnotation(fileNamePartitioned,'c20835db4b1b4e108828a8537ff41506','https://spor-sit.azure-api.net/pms/api/v2/',df,coll, index)
        try:
            pms_oms_annotation_data = documentAnnotationObj.processRegulatedAuthorizationForDoc()
            print(pms_oms_annotation_data)
        except Exception as e:
            pms_oms_annotation_data = None
            print("Error Found", str(e))
            
        print(f"Completed Document Annotation")        
        flowLogger.logFlowCheckpoint("Completed Document Annotation")
        metrics.getMetric(f"{index}: Document Annotation")
        
        print(f"Starting Extracting Content Between Heading For File :- {fileNamePartitioned}")        
        flowLogger.logFlowCheckpoint("Starting Extracting Content Between Heading")
        
        extractContentlogger =  MatchLogger(f'ExtractContentBetween_{index}_{getRandomString(1)}', fileNamePartitioned, domain, procedureType, languageCode, index, fileNameLog)
        extractorObj = DataBetweenHeadingsExtractor(extractContentlogger, basePath, coll)
        dfExtractedHierRR = extractorObj.extractContentBetweenHeadings(fileNamePartitioned)
        
        print(f"Completed Extracting Content Between Heading")        
        flowLogger.logFlowCheckpoint("Completed Extracting Content Between Heading")
        metrics.getMetric(f"{index}: Content Extraction")
        
        
        xmlLogger =  MatchLogger(f'XmlGeneration_{index}_{getRandomString(1)}', fileNamePartitioned, domain, procedureType, languageCode, index, fileNameLog)
        fhirXmlGeneratorObj = FhirXmlGenerator(xmlLogger, controlBasePath, basePath, pms_oms_annotation_data, stylesFilePath, medName)
        fileNameXml = fileNamePartitioned.replace('.json','.xml')
        generatedXml = fhirXmlGeneratorObj.generateXml(dfExtractedHierRR, fileNameXml)
        
        metrics.getMetric(f"{index}: Generate XML")
        
        fhirServiceLogger =  MatchLogger(f'XML Submission Logger_{index}_{getRandomString(1)}', fileNamePartitioned, domain, procedureType, languageCode, index, fileNameLog)
        
        fhirServiceObj = FhirService(fhirServiceLogger, apiMmgtBaseUrl, addBundleApiEndPointUrlSuffix, apiMmgtSubsKey, basePath, generatedXml)
        fhirServiceObj.submitFhirXml()
        
        
        
        
        metrics.getMetric(f"{index}: Submit FHIR Msg")
        
        print(f"Created XML File For :- {fileNamePartitioned}")
        
        flowLogger.logFlowCheckpoint("Starting list bundle update/addition")
        if documentAnnotationObj.listRegulatedAuthorizationIdentifiers != None:
            for id in documentAnnotationObj.listRegulatedAuthorizationIdentifiers:
                listRegulatedAuthCodesAccrossePI.append(id)
        listBundleLogger =  MatchLogger(f'List Bundle Creation Logger_{index}_{getRandomString(1)}', fileNamePartitioned, domain, procedureType, languageCode, index, fileNameLog)
        print("\nlistRegulatedAuthCodesAccrossePI",listRegulatedAuthCodesAccrossePI)
        try:
            listBundleHandler = ListBundleHandler(listBundleLogger,
                     domain,
                     procedureType,
                     index,
                     documentType,
                     languageCode,
                     medName,
                     controlBasePath,
                     jsonTempFileName,
                     listBundleDocumentTypeCodesFileName,
                     fileNameDocumentTypeNames,
                     listRegulatedAuthCodesAccrossePI,
                     apiMmgtBaseUrl,
                     getListApiEndPointUrlSuffix,
                     addUpdateListApiEndPointUrlSuffix,
                     apiMmgtSubsKey)

            listBundleXml = listBundleHandler.addOrUpdateDocumentItem(str(fhirServiceObj.SubmittedFhirMsgRefId))
            listBundleHandler.submitListXmLToServer(listBundleXml)

            flowLogger.logFlowCheckpoint("Completed list bundle update/addition")
            metrics.getMetric(f"{index}: Update/Add List Bundle")
            #return df,coll,dfExtractedHierRR
        except Exception as e:
            print(str(e))
            if 'No MAN Code found' in str(e):
                flowLogger.logFlowCheckpoint("Skipping list bundle addtion/update as no MAN found")
            
    
    flowLogger.logFlowCheckpoint("Completed Processing Partitioned Jsons")
    metrics.getMetric(f"{index}: Completed")
    metrics.end()

In [33]:
#from wordToHtmlConvertor.wordToHtmlConvertor import WordToHtmlConvertor
#
#wordToHtmlConvertorObj = WordToHtmlConvertor()
#wordToHtmlConvertorObj.convertWordToHTML()

In [34]:
def runAll(inputList):
    for inputDoc in inputList:
        # inputZipFolderPath = "F:\Projects\EMA\Repository\EMA EPI PoC\\function_code\\inputblob"
        inputZipFolderPath = os.path.abspath(os.path.join('..'))
        inputZipFolderPath = os.path.join(inputZipFolderPath, 'inputblob')
        inputZipFileName = inputDoc

        fileNameQrd = 'qrd_canonical_model.csv'
        fileNameMatchRuleBook = 'ruleDict.json'
        fileNameDocumentTypeNames = 'documentTypeNames.json'
        fsMountName = '/mounted'
        jsonTempFileName = 'listBundleJsonTemplate.json'
        listBundleDocumentTypeCodesFileName = 'listBundleDocumentTypeCodes.json'
        apiMmgtBaseUrl = "https://ema-dap-epi-dev-fhir-apim.azure-api.net"
        getListApiEndPointUrlSuffix = "/epi/v1/List"
        addUpdateListApiEndPointUrlSuffix = "/epi-w/v1/List"
        addBundleApiEndPointUrlSuffix = "/epi-w/v1/Bundle"
        apiMmgtSubsKey = "ba6d7e9a73ed4facaa58fc983bf6db50"



        info = inputZipFileName.split("~")

        try:
            medName = info[0]
            domain = info[1]
            procedureType = info[2]
            languageCode = info[3]
            timestamp = info[4]
            timestamp = timestamp.replace(".zip","")

        except Exception:
            raise f"Missing required info in the zip file name {inputZipFileName}"

        if "\\" in os.getcwd():
            localEnv = True
            inputZipFolderPath = os.path.join(os.path.abspath(os.path.join('..')),inputZipFolderPath)
            outputFolderPath = os.path.join(os.path.abspath(os.path.join('..')), 'work', f"{domain}", f"{procedureType}", f"{medName}", f"{languageCode}", f"{timestamp}")
            controlFolderPath = os.path.join(os.path.abspath(os.path.join('..')),'control')
        else:
            localEnv = False
            inputZipFolderPath = os.path.join(f'{fsMountName}',inputZipFolderPath)
            outputFolderPath = os.path.join(f'{fsMountName}', 'work', f"{domain}", f"{procedureType}", f"{medName}", f"{languageCode}", f"{timestamp}")
            controlFolderPath = os.path.join(f'{fsMountName}','control')


        print(inputZipFileName, inputZipFolderPath, outputFolderPath, controlFolderPath)

        mode = 0o666

        if localEnv is True:
            inputZipFolderPath = inputZipFolderPath.replace("/","\\")
            outputFolderPath = outputFolderPath.replace("/","\\")
            controlFolderPath = controlFolderPath.replace("/","\\")

        try:
            os.makedirs(inputZipFolderPath, mode)
            os.makedirs(outputFolderPath, mode)
            os.makedirs(controlFolderPath, mode)

        except Exception:
            print("Already Present")

        with zipfile.ZipFile(f'{inputZipFolderPath}/{inputZipFileName}',"r") as zip_ref:
                zip_ref.extractall(outputFolderPath)


        _,_,fileNames = next(os.walk(outputFolderPath))
        htmlFileName = [fileName for fileName in fileNames if ".htm" in fileName][0]

        print(htmlFileName)

        parseDocument(controlFolderPath,
                  outputFolderPath,
                  htmlFileName,
                  fileNameQrd,
                  fileNameMatchRuleBook,
                  fileNameDocumentTypeNames,
                  jsonTempFileName,
                  listBundleDocumentTypeCodesFileName,
                  apiMmgtBaseUrl,
                  getListApiEndPointUrlSuffix,
                  addUpdateListApiEndPointUrlSuffix,
                  addBundleApiEndPointUrlSuffix,
                  apiMmgtSubsKey,
                  medName)


In [5]:
inputList = ['GONAL-f~H~CAP~en~2021-06-04T08-55-59Z.zip',
    'GONAL-f~H~CAP~es~2021-06-06T11-29-47Z.zip',
    'GONAL-f~H~CAP~de~2021-06-07T06-58-30Z.zip']
runAll(inputList)

2021-06-08 01:04:46,825 : Flow Logger HTML_F : Starting HTML Conversion To Json | H | CAP |  en | HTML | gonal-f_clean.htm
2021-06-08 01:04:46,833 : Style Dictionary_h : Reading style dictionary in file: rule_dictionary_en.json | H | CAP |  en | HTML | gonal-f_clean.htm
2021-06-08 01:04:46,873 : Style Dictionary_h : Qrd Section Keys Retrieved For Style Dictionary: ANNEX I, ANNEX II, ANNEX III, B. PACKAGE LEAFLET | H | CAP |  en | HTML | gonal-f_clean.htm


GONAL-f~H~CAP~en~2021-06-04T08-55-59Z.zip F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z F:\Projects\EMA\Repository\EMA EPI PoC\function_code\control
Already Present
gonal-f_clean.htm
['F:', 'Projects', 'EMA', 'Repository', 'EMA EPI PoC', 'function_code', 'work', 'H', 'CAP', 'GONAL-f', 'en', '2021-06-04T08-55-59Z'] gonal-f_clean.htm
2021-06-04T08-55-59Z en GONAL-f CAP H
------------- F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z\outputJSON\gonal-f_clean.txt -----------------
F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z\gonal-f_clean.htm F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z\outputJSON\gonal-f_clean.json


2021-06-08 01:04:48,516 : Parser_c : Style Information Stored In File: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z\outputJSON\gonal-f_clean.txt | H | CAP |  en | HTML | gonal-f_clean.htm
2021-06-08 01:04:55,767 : Parser_c : Writing to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z\outputJSON\gonal-f_clean.json | H | CAP |  en | HTML | gonal-f_clean.htm
2021-06-08 01:04:56,280 : Flow Logger HTML_F : Completed HTML Conversion To Json | H | CAP |  en | HTML | gonal-f_clean.htm
2021-06-08 01:04:56,280 : Flow Logger HTML_F : HTML Conversion To Json,0.1576 Min,13.105251 MB,44.735048 MB,49.4%
 | H | CAP |  en | HTML | gonal-f_clean.htm
2021-06-08 01:04:56,292 : Flow Logger HTML_F : Starting Json Split | H | CAP |  en | HTML | gonal-f_clean.htm
2021-06-08 01:04:56,300 : Style Dictionary_N : Reading style dictionary in file: rule_dictionary_en.json | H | CAP |  en | Json | gonal-f_clean.js

stylePath:- F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z\outputJSON\gonal-f_clean.txt
Metrics : HTML Conversion To Json,0.1576 Min,13.105251 MB,44.735048 MB,49.4%

PathJson F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z\outputJSON\gonal-f_clean.json


2021-06-08 01:04:57,303 : Partition_t : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z\partitionedJSONs\gonal-f_clean_SmPC.json | H | CAP |  en | Json | gonal-f_clean.json
2021-06-08 01:04:57,448 : Partition_t : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z\partitionedJSONs\gonal-f_clean_ANNEX II.json | H | CAP |  en | Json | gonal-f_clean.json
2021-06-08 01:04:57,592 : Partition_t : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z\partitionedJSONs\gonal-f_clean_ANNEX III.json | H | CAP |  en | Json | gonal-f_clean.json
2021-06-08 01:04:57,608 : Partition_t : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\en\2021-06-04T08-55-59Z\partitionedJSONs\gonal-f_clean_ PACKAGE LEAFLET.json | H | CAP |  en | Json | gonal-

...

HTTP error occurred: 413 Client Error: Payload Too Large for url: https://ema-dap-epi-dev-fhir-apim.azure-api.net/epi-w/v1/Bundle
Error log: The requested resource exceeded the backing database's size limit.
Metrics : 3: Submit FHIR Msg,0.1517 Min,0.068488 MB,0.224394 MB,51.6%

Created XML File For :- gonal-f_clean_ PACKUNGSBEILAGE.json

listRegulatedAuthCodesAccrossePI ['EU/1/95/001/025', 'EU/1/95/001/026', 'EU/1/95/001/027', 'EU/1/95/001/021', 'EU/1/95/001/031', 'EU/1/95/001/000', 'EU/1/95/001/033', 'EU/1/95/001/034', 'EU/1/95/001/035', 'EU/1/95/001/025', 'EU/1/95/001/026', 'EU/1/95/001/027', 'EU/1/95/001/021', 'EU/1/95/001/031', 'EU/1/95/001/000', 'EU/1/95/001/033', 'EU/1/95/001/034', 'EU/1/95/001/035']


2021-06-08 01:42:37,431 : List Bundle Creation Logger_3_A : Getting list bundle for MAN EU/1/95/001/026  | H | CAP |  de | 3 | gonal-f_clean_ PACKUNGSBEILAGE.json
2021-06-08 01:42:38,300 : List Bundle Creation Logger_3_A : Getting list bundle for MAN EU/1/95/001/027  | H | CAP |  de | 3 | gonal-f_clean_ PACKUNGSBEILAGE.json
2021-06-08 01:42:39,160 : List Bundle Creation Logger_3_A : Getting list bundle for MAN EU/1/95/001/021  | H | CAP |  de | 3 | gonal-f_clean_ PACKUNGSBEILAGE.json
2021-06-08 01:42:40,128 : List Bundle Creation Logger_3_A : Getting list bundle for MAN EU/1/95/001/031  | H | CAP |  de | 3 | gonal-f_clean_ PACKUNGSBEILAGE.json
2021-06-08 01:42:41,043 : List Bundle Creation Logger_3_A : Getting list bundle for MAN EU/1/95/001/000  | H | CAP |  de | 3 | gonal-f_clean_ PACKUNGSBEILAGE.json
2021-06-08 01:42:41,908 : List Bundle Creation Logger_3_A : Getting list bundle for MAN EU/1/95/001/033  | H | CAP |  de | 3 | gonal-f_clean_ PACKUNGSBEILAGE.json
2021-06-08 01:42:42,88

Updating


2021-06-08 01:42:55,957 : List Bundle Creation Logger_3_A : List update successfully completed 4e8cd513-14c0-446b-915e-b46b0ee889a6 | H | CAP |  de | 3 | gonal-f_clean_ PACKUNGSBEILAGE.json
2021-06-08 01:42:55,957 : Flow Logger HTML_w : Completed list bundle update/addition | H | CAP |  de | HTML | gonal-f_clean.htm
2021-06-08 01:42:55,965 : Flow Logger HTML_w : 3: Update/Add List Bundle,0.3252 Min,0.329406 MB,0.480429 MB,52.1%
 | H | CAP |  de | HTML | gonal-f_clean.htm
2021-06-08 01:42:55,965 : Flow Logger HTML_w : Completed Processing Partitioned Jsons | H | CAP |  de | HTML | gonal-f_clean.htm
2021-06-08 01:42:55,965 : Flow Logger HTML_w : 3: Completed,0.0 Min,0.149713 MB,0.151703 MB,52.1%
 | H | CAP |  de | HTML | gonal-f_clean.htm
2021-06-08 01:42:55,973 : Flow Logger HTML_w : Final Metrics,13.0941 Min,0.0 MB,62.715329 MB,55.7%
 | H | CAP |  de | HTML | gonal-f_clean.htm


Metrics : 3: Update/Add List Bundle,0.3252 Min,0.329406 MB,0.480429 MB,52.1%

Metrics : 3: Completed,0.0 Min,0.149713 MB,0.151703 MB,52.1%

Metrics : Final Metrics,13.0941 Min,0.0 MB,62.715329 MB,55.7%



In [12]:
inputList = ['Ovaleap~H~CAP~de~2021-06-07T08-05-21Z.zip',
            'Ovaleap~H~CAP~en~2021-06-04T08-18-55Z.zip',
            'Ovaleap~H~CAP~es~2021-06-07T11-37-57Z.zip']
runAll(inputList)

2021-06-08 01:44:18,621 : Flow Logger HTML_z : Starting HTML Conversion To Json | H | CAP |  de | HTML | Ovaleap_clean.htm
2021-06-08 01:44:18,629 : Style Dictionary_3 : Reading style dictionary in file: rule_dictionary_de.json | H | CAP |  de | HTML | Ovaleap_clean.htm
2021-06-08 01:44:18,661 : Style Dictionary_3 : Qrd Section Keys Retrieved For Style Dictionary: ANHANG I, ANHANG II, ANHANG III, B. PACKUNGSBEILAGE | H | CAP |  de | HTML | Ovaleap_clean.htm


Ovaleap~H~CAP~de~2021-06-07T08-05-21Z.zip F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\de\2021-06-07T08-05-21Z F:\Projects\EMA\Repository\EMA EPI PoC\function_code\control
Already Present
Ovaleap_clean.htm
['F:', 'Projects', 'EMA', 'Repository', 'EMA EPI PoC', 'function_code', 'work', 'H', 'CAP', 'Ovaleap', 'de', '2021-06-07T08-05-21Z'] Ovaleap_clean.htm
2021-06-07T08-05-21Z de Ovaleap CAP H
------------- F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\de\2021-06-07T08-05-21Z\outputJSON\Ovaleap_clean.txt -----------------
F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\de\2021-06-07T08-05-21Z\Ovaleap_clean.htm F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\de\2021-06-07T08-05-21Z\outputJSON\Ovaleap_clean.json


2021-06-08 01:44:19,184 : Parser_N : Style Information Stored In File: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\de\2021-06-07T08-05-21Z\outputJSON\Ovaleap_clean.txt | H | CAP |  de | HTML | Ovaleap_clean.htm
2021-06-08 01:44:22,309 : Parser_N : Writing to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\de\2021-06-07T08-05-21Z\outputJSON\Ovaleap_clean.json | H | CAP |  de | HTML | Ovaleap_clean.htm
2021-06-08 01:44:22,515 : Flow Logger HTML_z : Completed HTML Conversion To Json | H | CAP |  de | HTML | Ovaleap_clean.htm
2021-06-08 01:44:22,515 : Flow Logger HTML_z : HTML Conversion To Json,0.0649 Min,5.319709 MB,8.056129 MB,52.5%
 | H | CAP |  de | HTML | Ovaleap_clean.htm
2021-06-08 01:44:22,523 : Flow Logger HTML_z : Starting Json Split | H | CAP |  de | HTML | Ovaleap_clean.htm
2021-06-08 01:44:22,531 : Style Dictionary_p : Reading style dictionary in file: rule_dictionary_de.json | H | CAP |  de | Json | Ovaleap_clean.json

stylePath:- F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\de\2021-06-07T08-05-21Z\outputJSON\Ovaleap_clean.txt
Metrics : HTML Conversion To Json,0.0649 Min,5.319709 MB,8.056129 MB,52.5%

PathJson F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\de\2021-06-07T08-05-21Z\outputJSON\Ovaleap_clean.json


2021-06-08 01:44:22,758 : Partition_T : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\de\2021-06-07T08-05-21Z\partitionedJSONs\Ovaleap_clean_ANHANG II.json | H | CAP |  de | Json | Ovaleap_clean.json
2021-06-08 01:44:22,822 : Partition_T : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\de\2021-06-07T08-05-21Z\partitionedJSONs\Ovaleap_clean_ANHANG III.json | H | CAP |  de | Json | Ovaleap_clean.json
2021-06-08 01:44:22,826 : Partition_T : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\de\2021-06-07T08-05-21Z\partitionedJSONs\Ovaleap_clean_ PACKUNGSBEILAGE.json | H | CAP |  de | Json | Ovaleap_clean.json
2021-06-08 01:44:22,834 : Flow Logger HTML_z : ['Ovaleap_clean_SmPC.json', 'Ovaleap_clean_ANHANG II.json', 'Ovaleap_clean_ANHANG III.json', 'Ovaleap_clean_ PACKUNGSBEILAGE.json'] | H | CAP |  de | HTML | Ovaleap_clean.htm
2021-06-08 

...

POST sucessful: XML added with id f5cb8e41-db4c-456a-a68a-503a63282ea6
Metrics : 3: Submit FHIR Msg,0.0389 Min,0.195055 MB,0.675347 MB,53.5%

Created XML File For :- Ovaleap_clean_ PROSPECTO.json

listRegulatedAuthCodesAccrossePI ['EU/1/13/871/001', 'EU/1/13/871/002', 'EU/1/13/871/003', 'EU/1/13/871/001', 'EU/1/13/871/002', 'EU/1/13/871/003']


2021-06-08 01:55:13,754 : List Bundle Creation Logger_3_B : Getting list bundle for MAN EU/1/13/871/002  | H | CAP |  es | 3 | Ovaleap_clean_ PROSPECTO.json
2021-06-08 01:55:14,771 : List Bundle Creation Logger_3_B : Getting list bundle for MAN EU/1/13/871/003  | H | CAP |  es | 3 | Ovaleap_clean_ PROSPECTO.json
2021-06-08 01:55:15,866 : List Bundle Creation Logger_3_B : Getting list bundle for MAN EU/1/13/871/001  | H | CAP |  es | 3 | Ovaleap_clean_ PROSPECTO.json
2021-06-08 01:55:17,282 : List Bundle Creation Logger_3_B : Getting list bundle for MAN EU/1/13/871/002  | H | CAP |  es | 3 | Ovaleap_clean_ PROSPECTO.json
2021-06-08 01:55:18,298 : List Bundle Creation Logger_3_B : Getting list bundle for MAN EU/1/13/871/003  | H | CAP |  es | 3 | Ovaleap_clean_ PROSPECTO.json
2021-06-08 01:55:19,582 : List Bundle Creation Logger_3_B : Getting Existing List Bundle using common list id c4c8ded9-3b93-45cf-8b0c-da97308ee903 | H | CAP |  es | 3 | Ovaleap_clean_ PROSPECTO.json
2021-06-08 01:55

Updating


2021-06-08 01:55:21,883 : List Bundle Creation Logger_3_B : List update successfully completed c4c8ded9-3b93-45cf-8b0c-da97308ee903 | H | CAP |  es | 3 | Ovaleap_clean_ PROSPECTO.json
2021-06-08 01:55:21,891 : Flow Logger HTML_v : Completed list bundle update/addition | H | CAP |  es | HTML | Ovaleap_clean.htm
2021-06-08 01:55:21,891 : Flow Logger HTML_v : 3: Update/Add List Bundle,0.1535 Min,0.151687 MB,0.33926 MB,53.5%
 | H | CAP |  es | HTML | Ovaleap_clean.htm
2021-06-08 01:55:21,899 : Flow Logger HTML_v : Completed Processing Partitioned Jsons | H | CAP |  es | HTML | Ovaleap_clean.htm
2021-06-08 01:55:21,907 : Flow Logger HTML_v : 3: Completed,0.0001 Min,0.149385 MB,0.151623 MB,53.5%
 | H | CAP |  es | HTML | Ovaleap_clean.htm
2021-06-08 01:55:21,907 : Flow Logger HTML_v : Final Metrics,3.7724 Min,0.0 MB,7.11086 MB,53.5%
 | H | CAP |  es | HTML | Ovaleap_clean.htm


Metrics : 3: Update/Add List Bundle,0.1535 Min,0.151687 MB,0.33926 MB,53.5%

Metrics : 3: Completed,0.0001 Min,0.149385 MB,0.151623 MB,53.5%

Metrics : Final Metrics,3.7724 Min,0.0 MB,7.11086 MB,53.5%



In [21]:
fp = open(os.path.join('F:\Projects\EMA\Repository\EMA EPI PoC\\function_code\work\H\CAP\Ovaleap\el\\2021-06-07T09-07-39Z\Ovaleap_clean.htm'), 'r')

In [83]:
with open(os.path.join('F:\Projects\EMA\Repository\EMA EPI PoC\\function_code\work\H\CAP\Ovaleap\el\\2021-06-07T09-07-39Z\Ovaleap_clean.htm'), 'rb') as fp:
    soup = BeautifulSoup(fp, "html.parser")

    soup = cleanHTML(soup)
    soup.body['id']=uuid.uuid4()

text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- ΠΑΡΑΡΤΗΜΑ
I
text:-  
text:- ΠΕΡΙΛΗΨΗ
ΤΩΝ
ΧΑΡΑΚΤΗΡΙΣΤΙΚΩΝ
ΤΟΥ ΠΡΟΪΟΝΤΟΣ
text:-  
text:- 

text:-  
text:-  
text:- 1.       
text:- ΟΝΟΜΑΣΙΑ
ΤΟΥ
ΦΑΡΜΑΚΕΥΤΙΚΟΥ
ΠΡΟΪΟΝΤΟΣ
text:-  
text:- Ovaleap 300 IU/0,5 ml
ενέσιμο
διάλυμα
text:- Ovaleap
450 IU/0,75 m
text:- l
text:-  ενέσιμο
διάλυμα
text:- Ovaleap
900 IU/1,5 m
text:- l
text:-  ενέσιμο
διάλυμα
text:-  
text:-  
text:- 2.       
text:- ΠΟΙΟΤΙΚΗ
ΚΑΙ ΠΟΣΟΤΙΚΗ
ΣΥΝΘΕΣΗ
text:-  
text:- Κάθε
ml του
διαλύματος
περιέχει 600 IU
(που
ισοδυναμούν με
44 μικρογραμμάρια)

text:- θυλακιοτροπίνης άλφα*.
text:-  
text:- .
text:-  
text:- Ovaleap 300 IU/0,5 ml
ενέσιμο
διάλυμα
text:- Κάθε
φυσίγγιο
περιέχει 300 IU
(που
ισοδυναμούν με
22 μικρογραμμάρια)

text:- θυλακιοτροπίνης άλφα σε 0,5 ml
ενέσιμου
διαλύματος.
text:-  
text:-  0,5 ml
ενέσιμου
δια

text:-  
text:- Εάν επιτευχθεί υπερβολική αντίδραση, η
θεραπεία πρέπει να διακοπεί και να μη χορηγηθεί hCG (βλέπε παράγραφο 4.4). Η θεραπεία πρέπει να ξαναρχίσει στον επόμενο κύκλο σε δόση χαμηλότερη
από εκείνη του προηγούμενου κύκλου.
text:-  
text:-  
text:-  
text:-  
text:- 

text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- . 
text:-  
text:-  
text:-  
text:-  
text:-  
text:- στο
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- το
text:-  
text:-  
text:- .
text:-  
text:- Γυναίκες που
υποβάλλονται σε διέγερση των ωοθηκών για ανάπτυξη πολλαπλών ωοθυλακίων πριν από την in vitro γονιμοποίηση ή
άλλες ART
text:-  
text:- που

text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- 

text:- ART
text:- Η συνήθης δοσολογία για υπερωορρηξία περιλαμβάνει τη χορήγηση 150‑225 IU
θυλακιοτροπίνης
άλφα
ημερησίως, ξεκινώντας την ημέρα 2
ή 3 του κύκλου

text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- 
ταυτόχρονα
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- . 
text:-  
text:-  
text:-  
text:-  
text:- του

text:-  
text:- τ
text:-  
text:- 

text:-  
text:-  
text:-  
text:- 

text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- Η 
text:-  
text:-  
text:-  
text:- ότ
text:-  
text:-  
text:-  
text:- 1
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- .
text:-  
text:- Ειδικός
πληθυσμός
text:-  
text:- Ηλικιωμένος
πληθυσμός
text:- Δεν υπάρχει σχετική χρήση της θυλακιοτροπίνης
άλφα στον ηλικιωμένο πληθυσμό. Η ασφάλεια και η
αποτελεσματικότητα της θυλακιοτροπίνης
άλφα δεν έχουν
τεκμηριωθεί σε ηλικιωμένους ασθενείς.
text:-  
text:-  
text:-  
text:-  της 
text:- θυλακιοτροπίνης
άλφα στο
text:-  
text:-  
text:- ό
text:- . 
text:-  
text:-  
text:-  
text:-  της 
text:- θυλακιοτροπίνης
άλφα 
text:-  
text:- 

text:-  
text:-  
text:-  
text:- .
text:-  
text:- Νεφρική
ή ηπ

text:-  
text:-  
text:-  
text:-  
text:-  
text:- ‑
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- .
text:-  
text:- Δεν έχει γίνει άμεση σύγκριση της θυλακιοτροπίνης
άλφα/LH έναντι της ανθρώπινης εμμηνοπαυσιακής
γοναδοτροπίνης (hMG). Η αναδρομική σύγκριση με παλαιότερα στοιχεία υποδεικνύει ότι το ποσοστό
ωορρηξιών που παρατηρείται με θυλακιοτροπίνη
άλφα/LH είναι παρεμφερές με αυτό που λαμβάνεται με hMG.
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- . 
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- ότ
text:-  
text:- τ
text:-  
text:- ο
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- .
text:-  
text:- Σύνδρομο Υπερδιέγερσης των Ωοθηκών (OHSS)
text:-  
text:-  
text:-  
text:-  
text:- Κάποια
διόγκωση των
ωοθηκών είναι
μια προβλεπόμενη
επίδραση της
ελεγχόμενης
ωοθηκικής
διέγερσης. 
text:- Παρατηρείται πιο 

text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- ς
text:- .
text:-  
text:- Οι
ασθενείς θα
πρέπει να ενημερώνονται
για τον πιθανό
κίνδυνο
πολυδύμου κυήσεως
πριν από την
έναρξη της
θεραπείας.
text:-  
text:- Απώλεια κύησης
text:-  
text:- Η συχνότητα της απώλειας κύησης με αποβολή ή
αυτόματη έκτρωση είναι υψηλότερη σε ασθενείς
που υποβάλλονται σε διέγερση ωοθυλακικής ανάπτυξης για επαγωγή της ωορρηξίας ή ART απ’ ό,τι μετά από φυσιολογική σύλληψη.
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- π
text:-  
text:- ό
text:- τι 
text:-  
text:-  
text:-  
text:- .
text:-  
text:- Έκτοπη
κύηση
text:- Οι
γυναίκες με ιστορικό νόσου των σαλπίγγων βρίσκονται σε κίνδυνο έκτοπης κυήσεως είτε εάν η κύηση έχει επιτευχθεί με αυτόματη σύλληψη ή
κατόπιν θεραπείας υπογονιμότητας. Έχει αναφερθεί
πως ο
επ

...

text:- στο
text:-  
text:-  
text:-  
text:-  (
text:-  
text:- του

text:- ·           

text:-            

text:- εάν είστε γυναίκα
με:
text:- -       

text:-        

text:- διογκωμένες ωοθήκες ή
σάκκους με υγρό στο εσωτερικό των ωοθηκών
(κύστεις των
ωοθηκών)
άγνωστης αιτιολογίας.
text:-  
text:- ο
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- ο
text:-  
text:- ο
text:- ν
text:-  
text:- ς
text:- -       

text:-        

text:- γυναικολογική αιμορραγία άγνωστης αιτιολογίας.
text:-  
text:-  
text:-  
text:- ς
text:- -       

text:-        

text:- καρκίνο στις ωοθήκες, μήτρα ή
μαστούς.
text:-  
text:-  
text:- ο
text:-  
text:-  
text:- ς
text:- -       

text:-        

text:- οποιαδήποτε
κατάσταση που καθιστά αδύνατη την κύηση, όπως ανεπάρκεια των ωοθηκών (πρώιμη
εμμηνόπαυση), ινομυώματα
της μήτρας ή
δυσπλασία των γεννητικών οργάνων.
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- ω
text:-  
text:-  
text:-  
text:- ο
text:-  
text:- ινομυώ

text:- ·          

text:-           

text:- Εάν
χρησιμοποιήσετε
Ovaleap με άλλα σκευάσματα που βοηθούν την ωορρηξία
όπως ανθρώπινη
χοριακή
γοναδοτροπίνη
(hCG) ή κιτρική κλομιφαίνη,
αυτό μπορεί να αυξήσει την ανταπόκριση των ωοθυλακίων
σας.
text:- 

text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- ο
text:- ·          

text:-           

text:- Εάν
χρησιμοποιήσετε
Ovaleap ταυτόχρονα με έναν αγωνιστή ή
ανταγωνιστή της «εκλυτικής
ορμόνης των γοναδοτροπινών» (GnRH) (αυτά τα σκευάσματα μειώνουν τα επίπεδα των
σεξουαλικών ορμονών και σταματούν την ωορρηξία σας) μπορεί να χρειαστείτε μια υψηλότερη
δόση του Ovaleap
για να παράγετε ωοθυλάκια.
text:- 

text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- «
text:-  
text:-  
text:- ν
text:-  
text:-  
text:-  
text:- τ
text:-  
text:-  
text:-  
text:- τ
text:-  
text:-  
text:-  
text:- ώ
text:-  
text:-  
text:-  
text:-  
text:-  
text:- ς
text:-  
te

text:- 

text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- Εάν ο γιατρός σας δεν εντοπίσει μια απόκριση μετά από 5 εβδομάδες,
θα πρέπει να
σταματήσει αυτόν το θεραπευτικό κύκλο.
Για τον επόμενο κύκλο, ο
γιατρός σας θα σας χορηγήσει μια υψηλότερη αρχική δόση αυτού
του φαρμάκου
από πριν.
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- ς
text:- 

text:-  
text:-  
text:-  
text:-  
text:- τ
text:-  
text:-  
text:-  
text:- το
text:-  
text:-  
text:- ο
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- Εάν ο
οργανισμός σας παρουσιάσει υπερβολική απόκριση, η
θεραπεία σας
με το Ovaleap θα διακοπεί και δεν θα σας χορηγηθεί
hCG [βλ. επίσης
παράγραφο 2
κάτω από τον
τίτλο
«Σύνδρομο
Υπερδιέγερσης
των Ωοθηκών (OHSS)»].
Για τον επόμενο κύκλο, ο
γιατρός σας θα σας χορηγήσει
χαμη

text:- το
text:-  
text:-  
text:-  
text:- ν
text:- ·               

text:-                

text:- Ακμή
text:- ·               

text:-                

text:- Αύξηση
σωματικού
βάρους
text:- Πολύ σπάνιες
text:-  (μπορεί να
επηρεάσουν έως
1 στα 10.000 άτομα)
text:- ·               

text:-                

text:- Το άσθμα σας μπορεί να χειροτερέψει.
text:-  
text:-  
text:-  
text:-  
text:-  
text:-  
text:- Αναφορά
ανεπιθύμητων
ενεργειών
text:- Εάν
παρατηρήσετε
κάποια
ανεπιθύμητη
ενέργεια, ενημερώστε
τον γιατρό, τον
φαρμακοποιό ή
τον/την νοσοκόμο
σας. Αυτό
ισχύει και για
κάθε πιθανή
ανεπιθύμητη
ενέργεια που
δεν αναφέρεται
στο παρόν
φύλλο οδηγιών
χρήσης. Μπορείτε
επίσης να
αναφέρετε
ανεπιθύμητες
ενέργειες απευθείας,
μέσω του
εθνικού
συστήματος
αναφοράς που
αναγράφεται
στο 
text:- του
εθνικού
συστήματος
αναφοράς που
αναγράφεται
στο 
text:- Παράρτημα V
text:- Παράρτημα V
text:- .
text:-  Μέσω της
αναφοράς
ανεπιθύμητων
ενεργειών
μπορείτε να
βοηθήσετε στη
συλλογή
περισσότερων
πληροφοριώ

text:- Αναφορά ανεπιθύμητων ενεργειών
text:- 5.       
text:- Πώς να φυλάσσετε το Ovaleap
text:- 6.       
text:- Περιεχόμενα της συσκευασίας και λοιπές πληροφορίες
text:- Τι περιέχει το Ovaleap
text:- Εμφάνιση του Ovaleap και περιεχόμενα της συσκευασίας
text:- Κάτοχος Άδειας Κυκλοφορίας
text:- Παρασκευαστής
text:- Το παρόν φύλλο οδηγιών χρήσης αναθεωρήθηκε για τελευταία φορά στις {μήνας ΕΕΕΕ}.
text:- Γυναίκεςμεανωορρηξία(που περιλαμβάνεικαισύνδρομοπολυκυστικώνωοθηκών)
text:- 
text:- Γυναίκεςπου υποβάλλονταισεδιέγερσητωνωοθηκώνγιαανάπτυξηπολλαπλώνωοθυλακίωνπριναπό τηνinvitroγονιμοποίησηήάλλες ART
text:- 
text:- ΓυναίκεςμεανωορρηξίααπόβαρείαανεπάρκειαLHκαιFSH
text:- 
text:- Άνδρες με υπογοναδοτροπικό υπογοναδισμό
text:- Ειδικός πληθυσμός
text:- 
text:- 
text:- Τρόπος χορήγησης
text:- Ιχνηλασιμότητα
text:- Γενικά
text:- Πορφυρία
text:- Θεραπείαστιςγυναίκες
text:- 
text:- ΣύνδρομοΥπερδιέγερσηςτωνΩοθηκών(OHSS)
text:- Πολύδυμηκύηση
text:- 
text:- Απώλειακύησης
text:- 
text:- Έκτοπη κύηση
te

In [84]:
soup.find_all('b')

[<b><span lang="EL">ΠΑΡΑΡΤΗΜΑ I</span></b>,
 <b><span lang="EL">1.       </span></b>,
 <b><span lang="EL">ΟΝΟΜΑΣΙΑ ΤΟΥ ΦΑΡΜΑΚΕΥΤΙΚΟΥ ΠΡΟΪΟΝΤΟΣ</span></b>,
 <b><span lang="EL">2.       </span></b>,
 <b><span lang="EL">ΠΟΙΟΤΙΚΗ ΚΑΙ ΠΟΣΟΤΙΚΗ ΣΥΝΘΕΣΗ</span></b>,
 <b><span lang="EL">3.       </span></b>,
 <b><span lang="EL">ΦΑΡΜΑΚΟΤΕΧΝΙΚΗ ΜΟΡΦΗ</span></b>,
 <b><span lang="EL" style="text-transform:uppercase">4.       </span></b>,
 <b><span lang="EL">ΚΛΙΝΙΚΕΣ ΠΛΗΡΟΦΟΡΙΕΣ</span></b>,
 <b><span lang="EL">4.1     </span></b>,
 <b><span lang="EL">Θεραπευτικές ενδείξεις</span></b>,
 <b><span lang="EL">4.2     </span></b>,
 <b><span lang="EL">Δοσολογία και τρόπος χορήγησης</span></b>,
 <b><span lang="EL">4.3     </span></b>,
 <b><span lang="EL">Αντενδείξεις</span></b>,
 <b><span lang="EL">4.4     </span></b>,
 <b><span lang="EL">Ειδικές προειδοποιήσεις και προφυλάξεις κατά τη χρήση</span></b>,
 <b><span lang="EL">4.5     </span></b>,
 <b><span lang="EL">Αλληλεπιδράσεις με άλλα φαρμακευτικά προϊόντ

In [23]:
from bs4 import NavigableString, BeautifulSoup

In [35]:
soup = BeautifulSoup(fp, "html.parser")


In [82]:
def cleanHTML(soup):
    """
        Function to remove empty tags in HTML
    """
    remove_tags_in = ['span', 'b', 'em', 'i', 'u']
    for tag in remove_tags_in:
        for tag_dom in soup.body.find_all(tag):
            print("text:-",tag_dom.text)
            dom_children = tag_dom.findChildren()
            if(len(dom_children)==0 ):
                text_in_tag = "".join([ text.replace("\n"," ").replace('\t',"").replace("\r","") for text in tag_dom.find_all(text=True, recursive=True)])
                if(text_in_tag.isspace() or len(text_in_tag)==0):
                    parent = tag_dom.parent
                    tag_dom.decompose()
                else:
                    tag_dom.string.replace_with(text_in_tag)
                
    return soup

In [43]:
type(soup)

bs4.BeautifulSoup

In [47]:
soup.body.find_all('p')

[<p align="center" class="MsoNormal" style="text-align:center"><b><span lang="EL"> </span></b></p>,
 <p align="center" class="MsoNormal" style="text-align:center"><b><span lang="EL"> </span></b></p>,
 <p align="center" class="MsoNormal" style="text-align:center"><b><span lang="EL"> </span></b></p>,
 <p align="center" class="MsoNormal" style="text-align:center"><b><span lang="EL"> </span></b></p>,
 <p align="center" class="MsoNormal" style="text-align:center"><b><span lang="EL"> </span></b></p>,
 <p align="center" class="MsoNormal" style="text-align:center"><b><span lang="EL"> </span></b></p>,
 <p align="center" class="MsoNormal" style="text-align:center"><b><span lang="EL"> </span></b></p>,
 <p align="center" class="MsoNormal" style="text-align:center"><b><span lang="EL"> </span></b></p>,
 <p align="center" class="MsoNormal" style="text-align:center"><b><span lang="EL"> </span></b></p>,
 <p align="center" class="MsoNormal" style="text-align:center"><b><span lang="EL"> </span></b></p>,


In [45]:
soup.body.find_all('p')

[<p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNormal" style="text-align:center"></p>,
 <p align="center" class="MsoNorma

In [8]:
inputList = ['Ovaleap~H~CAP~el~2021-06-07T09-07-39Z.zip']
runAll(inputList)

2021-06-08 03:54:30,695 : Flow Logger HTML_k : Starting HTML Conversion To Json | H | CAP |  el | HTML | Ovaleap_clean.htm
2021-06-08 03:54:30,703 : Style Dictionary_b : Reading style dictionary in file: rule_dictionary_el.json | H | CAP |  el | HTML | Ovaleap_clean.htm
2021-06-08 03:54:30,752 : Style Dictionary_b : Qrd Section Keys Retrieved For Style Dictionary: ΠΑΡΑΡΤΗΜΑ I, ΠΑΡΑΡΤΗΜΑ II, ΠΑΡΑΡΤΗΜΑ III, B. ΦΥΛΛΟ ΟΔΗΓΙΩΝ ΧΡΗΣΗΣ | H | CAP |  el | HTML | Ovaleap_clean.htm


Ovaleap~H~CAP~el~2021-06-07T09-07-39Z.zip F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\el\2021-06-07T09-07-39Z F:\Projects\EMA\Repository\EMA EPI PoC\function_code\control
Already Present
Ovaleap_clean.htm
['F:', 'Projects', 'EMA', 'Repository', 'EMA EPI PoC', 'function_code', 'work', 'H', 'CAP', 'Ovaleap', 'el', '2021-06-07T09-07-39Z'] Ovaleap_clean.htm
2021-06-07T09-07-39Z el Ovaleap CAP H
------------- F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\el\2021-06-07T09-07-39Z\outputJSON\Ovaleap_clean.txt -----------------
F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\el\2021-06-07T09-07-39Z\Ovaleap_clean.htm F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Ovaleap\el\2021-06-07T09-07-39Z\outputJSON\Ovaleap_clean.json
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:-

text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:- . 
Changed:- . 
text:- Σ
Changed:- Σ
text:-  
Changed:- 
text:-  
Changed:- 
text:- ς
Changed:- ς
text:- 

Changed:- 
text:-  
Changed:- 
text:- ο
Changed:- ο
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  LH < 1,2 IU/l.
Changed:-  LH < 1,2 IU/l.
text:-  
Changed:- 
text:- Στους

Changed:- Στους 
text:- ενήλικους άνδρες
Changed:- ενήλικους άνδρες
text:-  
Changed:- 
text:-  
Changed:- 
text:- ·           

Changed:- ·           

text:-            

Changed:- 
text:- Το Ovaleap 
Changed:- Το Ovaleap 
text:- ενδείκνυται, για τη διέγερση της σπερματογένεσης στους άνδρες που έχουν
συγγενή ή
επίκτητο υπογοναδοτροπικό υπογοναδισμό σε συνδυασμό με θεραπεία με
ανθρώπινη χοριακή γοναδοτροπίνη (hCG).
Changed:- ενδείκνυται, για τη διέγερση της σπερματογένεσης στους άνδρες που έχουν
συγγενή ή
επίκτητο υπογοναδοτ

text:-  
Changed:- 
text:- 37,
Changed:- 37,
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:- 

Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:- 1
Changed:- 1
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:- ς
Changed:- ς
text:- . 
Changed:- . 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:- ω
Changed:- ω
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:- του

Changed:- του 
text:-  
Changed:- 
text:- το
Changed:- το
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 

text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:- τ
Changed:- τ
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:- ς
Changed:- ς
text:- .
Changed:- .
text:-  
Changed:- 
text:- Γυναίκες με ανωορρηξία από βαρεία ανεπάρκεια LH και FSH
Changed:- Γυναίκες με ανωορρηξία από βαρεία ανεπάρκεια LH και FSH
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:-  
Changed:- 
text:- Σ
Changed:- Σ
text:- ε γυναίκες με ανεπάρκεια LH και FSH (υπογοναδοτροπικός υπογοναδισμός), ο
στόχος της θεραπείας
με θυλακιοτροπίνη
άλφα σε συνδυασμό με lutropin alfa είναι η
ανάπτυξη ενός ωρίμου Γραφιανού ωοθυλακίου από το οποίο θα απελευθερωθεί το ωοκύτταρο, κατόπιν χορήγησης hCG. Η
θυλακιοτροπίνη
άλφα πρέπει να χορη

...

POST sucessful: XML added with id fe6f3b10-84a7-4d17-a700-c17ed3c074f9
Metrics : 1: Submit FHIR Msg,0.0336 Min,0.240687 MB,0.693238 MB,52.6%

Created XML File For :- Ovaleap_clean_ΠΑΡΑΡΤΗΜΑ II.json

listRegulatedAuthCodesAccrossePI ['EU/1/13/871/001', 'EU/1/13/871/002', 'EU/1/13/871/003']


2021-06-08 03:57:09,572 : List Bundle Creation Logger_1_K : Getting list bundle for MAN EU/1/13/871/002  | H | CAP |  el | 1 | Ovaleap_clean_ΠΑΡΑΡΤΗΜΑ II.json
2021-06-08 03:57:10,406 : List Bundle Creation Logger_1_K : Getting list bundle for MAN EU/1/13/871/003  | H | CAP |  el | 1 | Ovaleap_clean_ΠΑΡΑΡΤΗΜΑ II.json
2021-06-08 03:57:11,298 : List Bundle Creation Logger_1_K : Getting Existing List Bundle using common list id c4c8ded9-3b93-45cf-8b0c-da97308ee903 | H | CAP |  el | 1 | Ovaleap_clean_ΠΑΡΑΡΤΗΜΑ II.json
2021-06-08 03:57:12,149 : List Bundle Creation Logger_1_K : Added missing MAN identifiers | H | CAP |  el | 1 | Ovaleap_clean_ΠΑΡΑΡΤΗΜΑ II.json
2021-06-08 03:57:12,151 : List Bundle Creation Logger_1_K : Adding a new item | H | CAP |  el | 1 | Ovaleap_clean_ΠΑΡΑΡΤΗΜΑ II.json
2021-06-08 03:57:12,155 : List Bundle Creation Logger_1_K : Converted to required XML format | H | CAP |  el | 1 | Ovaleap_clean_ΠΑΡΑΡΤΗΜΑ II.json


Updating


2021-06-08 03:57:13,276 : List Bundle Creation Logger_1_K : List update successfully completed c4c8ded9-3b93-45cf-8b0c-da97308ee903 | H | CAP |  el | 1 | Ovaleap_clean_ΠΑΡΑΡΤΗΜΑ II.json
2021-06-08 03:57:13,277 : Flow Logger HTML_k : Completed list bundle update/addition | H | CAP |  el | HTML | Ovaleap_clean.htm
2021-06-08 03:57:13,278 : Flow Logger HTML_k : 1: Update/Add List Bundle,0.0772 Min,0.490838 MB,1.073798 MB,52.5%
 | H | CAP |  el | HTML | Ovaleap_clean.htm
2021-06-08 03:57:13,280 : Flow Logger HTML_k : Completed Processing Partitioned Jsons | H | CAP |  el | HTML | Ovaleap_clean.htm
2021-06-08 03:57:13,282 : Flow Logger HTML_k : 3: Completed,0.0 Min,0.003546 MB,0.15185 MB,52.5%
 | H | CAP |  el | HTML | Ovaleap_clean.htm
2021-06-08 03:57:13,283 : Flow Logger HTML_k : Final Metrics,2.709 Min,0.0 MB,12.774598 MB,53.5%
 | H | CAP |  el | HTML | Ovaleap_clean.htm


Metrics : 1: Update/Add List Bundle,0.0772 Min,0.490838 MB,1.073798 MB,52.5%

Index 2
Index 3
Metrics : 3: Completed,0.0 Min,0.003546 MB,0.15185 MB,52.5%

Metrics : Final Metrics,2.709 Min,0.0 MB,12.774598 MB,53.5%



In [ ]:
inputList = ['Ovaleap~H~CAP~el~2021-06-07T09-07-39Z.zip']
runAll(inputList)

In [ ]:
inputList = ['GONAL-f~H~CAP~el~2021-06-06T10-02-52Z.zip']
runAll(inputList)

2021-06-08 05:31:54,339 : Flow Logger HTML_D : Starting HTML Conversion To Json | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 05:31:54,348 : Style Dictionary_8 : Reading style dictionary in file: rule_dictionary_el.json | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 05:31:54,390 : Style Dictionary_8 : Qrd Section Keys Retrieved For Style Dictionary: ΠΑΡΑΡΤΗΜΑ Ι, ΠΑΡΑΡΤΗΜΑ ΙΙ, ΠΑΡΑΡΤΗΜΑ ΙΙΙ, Β. ΦΥΛΛΟ ΟΔΗΓΙΩΝ ΧΡΗΣΗΣ | H | CAP |  el | HTML | gonal-f_clean.htm


GONAL-f~H~CAP~el~2021-06-06T10-02-52Z.zip F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z F:\Projects\EMA\Repository\EMA EPI PoC\function_code\control
Already Present
gonal-f_clean.htm
['F:', 'Projects', 'EMA', 'Repository', 'EMA EPI PoC', 'function_code', 'work', 'H', 'CAP', 'GONAL-f', 'el', '2021-06-06T10-02-52Z'] gonal-f_clean.htm
2021-06-06T10-02-52Z el GONAL-f CAP H
------------- F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\outputJSON\gonal-f_clean.txt -----------------
F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\gonal-f_clean.htm F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\outputJSON\gonal-f_clean.json


2021-06-08 05:31:59,717 : Parser_H : Style Information Stored In File: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\outputJSON\gonal-f_clean.txt | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 05:32:15,578 : Parser_H : Writing to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\outputJSON\gonal-f_clean.json | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 05:32:16,677 : Flow Logger HTML_D : Completed HTML Conversion To Json | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 05:32:16,681 : Flow Logger HTML_D : HTML Conversion To Json,0.3724 Min,24.449914 MB,63.954152 MB,53.8%
 | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 05:32:16,701 : Flow Logger HTML_D : Starting Json Split | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 05:32:16,709 : Style Dictionary_t : Reading style dictionary in file: rule_dictionary_el.json | H | CAP |  el | Json | gonal-f_clean.js

stylePath:- F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\outputJSON\gonal-f_clean.txt
Metrics : HTML Conversion To Json,0.3724 Min,24.449914 MB,63.954152 MB,53.8%

PathJson F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\outputJSON\gonal-f_clean.json


2021-06-08 05:32:17,696 : Partition_M : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\partitionedJSONs\gonal-f_clean_SmPC.json | H | CAP |  el | Json | gonal-f_clean.json
2021-06-08 05:32:17,985 : Partition_M : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\partitionedJSONs\gonal-f_clean_ΠΑΡΑΡΤΗΜΑ ΙΙ.json | H | CAP |  el | Json | gonal-f_clean.json
2021-06-08 05:32:18,271 : Partition_M : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\partitionedJSONs\gonal-f_clean_ΠΑΡΑΡΤΗΜΑ ΙΙΙ.json | H | CAP |  el | Json | gonal-f_clean.json
2021-06-08 05:32:18,292 : Partition_M : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\partitionedJSONs\gonal-f_clean_Β. ΦΥΛΛΟ ΟΔΗΓΙΩΝ ΧΡΗΣΗΣ.json | H | CAP |  el 

...

2021-06-08 05:35:53,663 : Heading Extraction gonal-f_clean_SmPC.json_J : Match Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | Doc txt :- '4.5 Αλληλεπιδράσεις με άλλα φαρμακευτικά προϊόντα και άλλες μορφές αλληλεπίδρασης' | Qrd txt :- '4.5 Αλληλεπιδράσεις με άλλα φαρμακευτικά προϊόντα και άλλες μορφές αλληλεπίδρασης' | Matched :- 'True'
2021-06-08 05:35:53,674 : Heading Extraction gonal-f_clean_SmPC.json_J : Validation Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | currHeadId :- '16020' | prevHeadingCurrId :- '16017' | prevHeadingFoundId :- '16017'
2021-06-08 05:35:54,040 : Heading Extraction gonal-f_clean_SmPC.json_J : Match Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | Doc txt :- '4.6 Γονιμότητα, κύηση και γαλουχία' | Qrd txt :- '4.6 Γονιμότητα, κύηση και γαλουχία' | Matched :- 'True'
2021-06-08 05:35:54,051 : Heading Extraction gonal-f_clean_SmPC.json_J : Validation Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | currHeadId :- '16022' | prevHeadingCurr

index                                         565
id                                          16022
domain                                          H
Procedure type                                CAP
Document type                                SmPC
Language code                                  el
Display code                                  4.6
Name               Γονιμότητα, κύηση και γαλουχία
parent_id                                 16009.0
Mandatory                                    True
heading_id                                     22
document_number                               0.0
Heading Level                                  L2
Name: 21, dtype: object
child list [index                  566
id                   16023
domain                   H
Procedure type         CAP
Document type         SmPC
Language code           el
Display code           NaN
Name                 Κύηση
parent_id          16022.0
Mandatory            False
heading_id              23
document_number  

2021-06-08 05:35:57,870 : Heading Extraction gonal-f_clean_SmPC.json_J : Match Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | Doc txt :- 'Γονιμότητα' | Qrd txt :- 'Γονιμότητα' | Matched :- 'True'
2021-06-08 05:35:57,915 : Heading Extraction gonal-f_clean_SmPC.json_J : Validation Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | currHeadId :- '16025' | prevHeadingCurrId :- '16022' | prevHeadingFoundId :- '16022'



OriginalCheck

index                                         565
id                                          16022
domain                                          H
Procedure type                                CAP
Document type                                SmPC
Language code                                  el
Display code                                  4.6
Name               Γονιμότητα, κύηση και γαλουχία
parent_id                                 16009.0
Mandatory                                    True
heading_id                                     22
document_number                               0.0
Heading Level                                  L2
Name: 21, dtype: object
child list [index                  566
id                   16023
domain                   H
Procedure type         CAP
Document type         SmPC
Language code           el
Display code           NaN
Name                 Κύηση
parent_id          16022.0
Mandatory            False
heading_id              23
d

2021-06-08 05:35:59,271 : Heading Extraction gonal-f_clean_SmPC.json_J : Match Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | Doc txt :- '4.7 Επιδράσεις στην ικανότητα οδήγησης και χειρισμού μηχανημάτων' | Qrd txt :- '4.7 Επιδράσεις στην ικανότητα οδήγησης και χειρισμού μηχανημάτων' | Matched :- 'True'
2021-06-08 05:35:59,287 : Heading Extraction gonal-f_clean_SmPC.json_J : Validation Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | currHeadId :- '16026' | prevHeadingCurrId :- '16022' | prevHeadingFoundId :- '16022'
2021-06-08 05:36:00,502 : Heading Extraction gonal-f_clean_SmPC.json_J : Match Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | Doc txt :- '4.8 Ανεπιθύμητες ενέργειες' | Qrd txt :- '4.8 Ανεπιθύμητες ενέργειες' | Matched :- 'True'
2021-06-08 05:36:00,521 : Heading Extraction gonal-f_clean_SmPC.json_J : Validation Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | currHeadId :- '16027' | prevHeadingCurrId :- '16026' | prevHeadingFoundId :- '16026'


In [22]:
inputList = ['GONAL-f~H~CAP~el~2021-06-06T10-02-52Z.zip']
runAll(inputList)

2021-06-08 04:48:12,590 : Flow Logger HTML_c : Starting HTML Conversion To Json | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 04:48:12,601 : Style Dictionary_Y : Reading style dictionary in file: rule_dictionary_el.json | H | CAP |  el | HTML | gonal-f_clean.htm


GONAL-f~H~CAP~el~2021-06-06T10-02-52Z.zip F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z F:\Projects\EMA\Repository\EMA EPI PoC\function_code\control
Already Present
gonal-f_clean.htm
['F:', 'Projects', 'EMA', 'Repository', 'EMA EPI PoC', 'function_code', 'work', 'H', 'CAP', 'GONAL-f', 'el', '2021-06-06T10-02-52Z'] gonal-f_clean.htm
2021-06-06T10-02-52Z el GONAL-f CAP H


2021-06-08 04:48:12,668 : Style Dictionary_Y : Qrd Section Keys Retrieved For Style Dictionary: ΠΑΡΑΡΤΗΜΑ I, ΠΑΡΑΡΤΗΜΑ II, ΠΑΡΑΡΤΗΜΑ III, B. ΦΥΛΛΟ ΟΔΗΓΙΩΝ ΧΡΗΣΗΣ | H | CAP |  el | HTML | gonal-f_clean.htm


------------- F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\outputJSON\gonal-f_clean.txt -----------------
F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\gonal-f_clean.htm F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\outputJSON\gonal-f_clean.json


2021-06-08 04:48:19,876 : Parser_o : Style Information Stored In File: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\outputJSON\gonal-f_clean.txt | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 04:48:42,634 : Parser_o : Writing to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\GONAL-f\el\2021-06-06T10-02-52Z\outputJSON\gonal-f_clean.json | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 04:48:44,182 : Flow Logger HTML_c : Completed HTML Conversion To Json | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 04:48:44,186 : Flow Logger HTML_c : HTML Conversion To Json,0.5266 Min,16.601639 MB,56.105608 MB,58.0%
 | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 04:48:44,212 : Flow Logger HTML_c : Starting Json Split | H | CAP |  el | HTML | gonal-f_clean.htm
2021-06-08 04:48:44,221 : Style Dictionary_k : Reading style dictionary in file: rule_dictionary_el.json | H | CAP |  el | Json | gonal-f_clean.js

...

2021-06-08 04:55:55,988 : Heading Extraction gonal-f_clean_SmPC.json_x : Match Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | Doc txt :- '9. ΗΜΕΡΟΜΗΝΙΑ ΠΡΩΤΗΣ ΕΓΚΡΙΣΗΣ/ΑΝΑΝΕΩΣΗΣ ΤΗΣ ΑΔΕΙΑΣ' | Qrd txt :- '9. ΗΜΕΡΟΜΗΝΙΑ ΠΡΩΤΗΣ ΕΓΚΡΙΣΗΣ/ΑΝΑΝΕΩΣΗΣ ΤΗΣ ΑΔΕΙΑΣ' | Matched :- 'True'
2021-06-08 04:55:55,998 : Heading Extraction gonal-f_clean_SmPC.json_x : Validation Flow Is Broken | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | currHeadId :- '16057' | prevHeadingCurrId :- '' | prevHeadingFoundId :- '16001'
2021-06-08 04:55:56,004 : Heading Extraction gonal-f_clean_SmPC.json_x : Validation Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | currHeadId :- '16057' | prevHeadingCurrId :- '16001' | prevHeadingFoundId :- '16001'
2021-06-08 04:55:56,009 : Heading Extraction gonal-f_clean_SmPC.json_x : Validation Failed By Style | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | currHeadId :- '16057' | prevHeadingCurrId :- '' | prevHeadingFoundId :- '16001'


----------------------------------
RemovedByStyle
----------------------------------


2021-06-08 04:55:58,873 : Heading Extraction gonal-f_clean_SmPC.json_x : Match Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | Doc txt :- '10. ΗΜΕΡΟΜΗΝΙΑ ΑΝΑΘΕΩΡΗΣΗΣ ΤΟΥ ΚΕΙΜΕΝΟΥ' | Qrd txt :- '10. ΗΜΕΡΟΜΗΝΙΑ ΑΝΑΘΕΩΡΗΣΗΣ ΤΟΥ ΚΕΙΜΕΝΟΥ' | Matched :- 'True'
2021-06-08 04:55:58,886 : Heading Extraction gonal-f_clean_SmPC.json_x : Validation Flow Is Broken | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | currHeadId :- '16058' | prevHeadingCurrId :- '' | prevHeadingFoundId :- '16001'
2021-06-08 04:55:58,895 : Heading Extraction gonal-f_clean_SmPC.json_x : Validation Passed | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | currHeadId :- '16058' | prevHeadingCurrId :- '16001' | prevHeadingFoundId :- '16001'
2021-06-08 04:55:58,900 : Heading Extraction gonal-f_clean_SmPC.json_x : Validation Failed By Style | H | CAP |  el | 0 | gonal-f_clean_SmPC.json | currHeadId :- '16058' | prevHeadingCurrId :- '' | prevHeadingFoundId :- '16001'


----------------------------------
RemovedByStyle
----------------------------------


KeyboardInterrupt: 

In [ ]:
inputList = ['Stalevo~H~CAP~el~2021-06-03T19-24-04Z.zip']
runAll(inputList)

In [17]:

inputList = ['Stalevo~H~CAP~en~2021-06-04T02-38-15Z.zip']
runAll(inputList)

2021-06-08 04:15:24,916 : Flow Logger HTML_T : Starting HTML Conversion To Json | H | CAP |  en | HTML | Stalevo_clean.htm
2021-06-08 04:15:24,923 : Style Dictionary_X : Reading style dictionary in file: rule_dictionary_en.json | H | CAP |  en | HTML | Stalevo_clean.htm
2021-06-08 04:15:24,985 : Style Dictionary_X : Qrd Section Keys Retrieved For Style Dictionary: ANNEX I, ANNEX II, ANNEX III, B. PACKAGE LEAFLET | H | CAP |  en | HTML | Stalevo_clean.htm


Stalevo~H~CAP~en~2021-06-04T02-38-15Z.zip F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Stalevo\en\2021-06-04T02-38-15Z F:\Projects\EMA\Repository\EMA EPI PoC\function_code\control
Already Present
Stalevo_clean.htm
['F:', 'Projects', 'EMA', 'Repository', 'EMA EPI PoC', 'function_code', 'work', 'H', 'CAP', 'Stalevo', 'en', '2021-06-04T02-38-15Z'] Stalevo_clean.htm
2021-06-04T02-38-15Z en Stalevo CAP H
------------- F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Stalevo\en\2021-06-04T02-38-15Z\outputJSON\Stalevo_clean.txt -----------------
F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Stalevo\en\2021-06-04T02-38-15Z\Stalevo_clean.htm F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Stalevo\en\2021-06-04T02-38-15Z\outputJSON\Stalevo_clean.json


2021-06-08 04:15:28,639 : Parser_w : Style Information Stored In File: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Stalevo\en\2021-06-04T02-38-15Z\outputJSON\Stalevo_clean.txt | H | CAP |  en | HTML | Stalevo_clean.htm


























ANNEX I

SUMMARY OF PRODUCT CHARACTERISTICS


1.      NAME OF THE MEDICINAL PRODUCT

Stalevo 50 mg/12.5 mg/200 mg film-coated tablets
Stalevo 75 mg/18.75 mg/200 mg film-coated tablets
Stalevo 100 mg/25 mg/200 mg film-coated tablets
Stalevo 125mg/31.25mg/200mg film-coated tablets
Stalevo 150 mg/37.5 mg/200 mg film-coated tablets
Stalevo 175 mg/43.75 mg/200 mg film-coated tablets
Stalevo 200 mg/50 mg/200 mg film-coated tablets 


2.      QUALITATIVE AND QUANTITATIVE COMPOSITION

50 mg/12.5 mg/200 mg
Each tablet contains 50 mg of levodopa, 12.5 mg of carbidopa and 200 mg of entacapone.

Excipient with known effect:
Each tablet contains 1.2 mg of sucrose.

75 mg/18.75 mg/200 mg
Each tablet contains 75 mg of levodopa, 18.75 mg of carbidopa and 200 mg of entacapone.

Excipient with known effect: 
Each tablet contains 1.4 mg of sucrose.

100 mg/25 mg/200 mg 
Each tablet contains 100 mg of levodopa, 25 mg of carbidopa and 200 mg of entacapone.

Excipient with known effe
























ANNEX I
ANNEX I
ANNEX I

SUMMARY OF PRODUCT CHARACTERISTICS
SUMMARY OF PRODUCT CHARACTERISTICS





1.      NAME OF THE MEDICINAL PRODUCT
1.      NAME OF THE MEDICINAL PRODUCT
1.      NAME OF THE MEDICINAL PRODUCT

Stalevo 50 mg/12.5 mg/200 mg film-coated tablets
Stalevo 50 mg/12.5 mg/200 mg film-coated tablets
Stalevo 75 mg/18.75 mg/200 mg film-coated tablets
Stalevo 75 mg/18.75 mg/200 mg film-coated tablets
Stalevo 100 mg/25 mg/200 mg film-coated tablets
Stalevo 100 mg/25 mg/200 mg film-coated tablets
Stalevo 125mg/31.25mg/200mg film-coated tablets
Stalevo 125
mg/31.25
mg/200
mg film-coated tablets
Stalevo 150 mg/37.5 mg/200 mg film-coated tablets
Stalevo 150 mg/37.5 mg/200 mg film-coated tablets
Stalevo 175 mg/43.75 mg/200 mg film-coated tablets
Stalevo 175 mg/43.75 mg/200 mg film-coated tablets
Stalevo 200 mg/50 mg/200 mg film-coated tablets 
Stalevo 200 mg/50 mg/200 mg film-coated tablets 


2.      QUALITATIVE AND QUANTITATIVE COMPOSITION
2.      QUALITATIV

...

2021-06-08 04:15:57,690 : Heading Extraction Stalevo_clean_SmPC.json_B : Started Extracting Heading | H | CAP |  en | 0 | Stalevo_clean_SmPC.json
2021-06-08 04:15:58,043 : Heading Extraction Stalevo_clean_SmPC.json_B : Match Passed | H | CAP |  en | 0 | Stalevo_clean_SmPC.json | Doc txt :- 'SUMMARY OF PRODUCT CHARACTERISTICS' | Qrd txt :- 'SUMMARY OF PRODUCT CHARACTERISTICS' | Matched :- 'True'
2021-06-08 04:15:58,051 : Heading Extraction Stalevo_clean_SmPC.json_B : Validation Passed As This The First Heading | H | CAP |  en | 0 | Stalevo_clean_SmPC.json | currHeadId :- '20001' | prevHeadingCurrId :- '' | prevHeadingFoundId :- ''
2021-06-08 04:15:58,116 : Heading Extraction Stalevo_clean_SmPC.json_B : Match Passed | H | CAP |  en | 0 | Stalevo_clean_SmPC.json | Doc txt :- '1. NAME OF THE MEDICINAL PRODUCT' | Qrd txt :- '1. NAME OF THE MEDICINAL PRODUCT' | Matched :- 'True'
2021-06-08 04:15:58,128 : Heading Extraction Stalevo_clean_SmPC.json_B : Validation Flow Is Broken | H | CAP |  en

2021-06-08 04:16:45,028 : Heading Extraction Stalevo_clean_SmPC.json_B : Match Passed In Lowercase  :  | H | CAP |  en | 0 | Stalevo_clean_SmPC.json | Doc txt :- '4.      Clinical particulars' | Qrd txt :- '4. CLINICAL PARTICULARS' | Matched :- 'True'
2021-06-08 04:16:45,039 : Heading Extraction Stalevo_clean_SmPC.json_B : Validation Passed | H | CAP |  en | 0 | Stalevo_clean_SmPC.json | currHeadId :- '20009' | prevHeadingCurrId :- '20008' | prevHeadingFoundId :- '20008'
2021-06-08 04:16:45,165 : Heading Extraction Stalevo_clean_SmPC.json_B : Match Passed | H | CAP |  en | 0 | Stalevo_clean_SmPC.json | Doc txt :- '4.1 Therapeutic indications' | Qrd txt :- '4.1 Therapeutic indications' | Matched :- 'True'
2021-06-08 04:16:45,180 : Heading Extraction Stalevo_clean_SmPC.json_B : Validation Passed | H | CAP |  en | 0 | Stalevo_clean_SmPC.json | currHeadId :- '20010' | prevHeadingCurrId :- '20009' | prevHeadingFoundId :- '20009'



OriginalCheck



2021-06-08 04:16:45,696 : Heading Extraction Stalevo_clean_SmPC.json_B : Match Passed | H | CAP |  en | 0 | Stalevo_clean_SmPC.json | Doc txt :- '4.2 Posology and method of administration' | Qrd txt :- '4.2 Posology and method of administration' | Matched :- 'True'
2021-06-08 04:16:45,708 : Heading Extraction Stalevo_clean_SmPC.json_B : Validation Passed | H | CAP |  en | 0 | Stalevo_clean_SmPC.json | currHeadId :- '20011' | prevHeadingCurrId :- '20010' | prevHeadingFoundId :- '20010'
2021-06-08 04:16:45,775 : Heading Extraction Stalevo_clean_SmPC.json_B : Match Passed | H | CAP |  en | 0 | Stalevo_clean_SmPC.json | Doc txt :- 'Posology' | Qrd txt :- 'Posology' | Matched :- 'True'
2021-06-08 04:16:45,794 : Heading Extraction Stalevo_clean_SmPC.json_B : Validation Failed As Current H3 Heading Is Not Part Of Valid H3 Headings in Previous H2 | H | CAP |  en | 0 | Stalevo_clean_SmPC.json | currHeadId :- '20012' | prevHeadingCurrId :- '20011' | prevHeadingFoundId :- '20011'


KeyboardInterrupt: 